In [14]:
import json
import glob
import pandas as pd
from collections import defaultdict
import tiktoken
import os
import time
import openai

## Loading Movie Metadata

In [15]:
summaries = []
for summary_path in glob.glob('data/movies/*/summary.json'):
    imdb_id = summary_path.split('/')[2].split('_')[0]
    with open(summary_path, 'r') as fp:
        summary = json.load(fp)
        summary['id'] = imdb_id
        summaries.append(summary)

In [16]:
df = pd.DataFrame(summaries)

In [17]:
df.head()

title                     genres          director   
0         The Hangover                     Comedy     Todd Phillips  \
1            Ladder 49    Action, Drama, Thriller       Jay Russell   
2  Mark of the Vampire            Horror, Mystery      Tod Browning   
3    The Mark of Zorro  Action, Adventure, Family  Rouben Mamoulian   
4      Son of Paleface            Comedy, Western     Frank Tashlin   

                                           starring rating   
0  Zach Galifianakis, Bradley Cooper, Justin Bartha    7.7  \
1   Joaquin Phoenix, John Travolta, Jacinda Barrett    6.5   
2    Lionel Barrymore, Elizabeth Allan, Bela Lugosi    6.3   
3       Tyrone Power, Linda Darnell, Basil Rathbone    7.5   
4                Bob Hope, Jane Russell, Roy Rogers    6.8   

                       release_date            runtime certificate   
0      June 5, 2009 (United States)  1 hour 40 minutes           R  \
1   October 1, 2004 (United States)  1 hour 55 minutes       PG-13   
2    April 26, 1935 (United States)             1 hour      Passed   
3  November 8, 1940 (United States)  1 hour 34 minutes    Approved   
4     July 14, 1952 (United States)  1 hour 35 minutes      Passed   

                                             img_url   
0  https://m.media-amazon.com/images/M/MV5BNGQwZj...  \
1  https://m.media-amazon.com/images/M/MV5BMjEyND...   
2  https://m.media-amazon.com/images/M/MV5BMTY4MT...   
3  https://m.media-amazon.com/images/M/MV5BMTU2OD...   
4  https://m.media-amazon.com/images/M/MV5BMzc1Nz...   

                                                plot         id  
0  Three buddies wake up from a bachelor party in...  tt1119646  
1  A firefighter, injured and trapped in a burnin...  tt0349710  
2  When a nobleman is murdered, a professor of th...  tt0026685  
3  A young Spanish aristocrat must masquerade as ...  tt0032762  
4  Junior Potter returns to claim his father's go...  tt0045177

In [18]:
df.shape

(10908, 11)

In [19]:
df.certificate.value_counts()[:10]

certificate
R            3838
PG-13        2063
PG           1298
Not Rated    1145
Approved      770
Passed        616
G             279
Unrated       163
TV-MA         152
TV-14          51
Name: count, dtype: int64

## Loading Movie Summary Data

In [20]:
def num_tokens_from_string(string: str, encoding_name: str) -> int:
    """Returns the number of tokens in a text string."""
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string))
    return num_tokens

import openai
from tenacity import retry, wait_random_exponential, stop_after_attempt


@retry(wait=wait_random_exponential(min=1, max=20), stop=stop_after_attempt(6))
def get_embedding(text: str, model="text-embedding-ada-002") -> list[float]:
    return openai.Embedding.create(input=[text], model=model)["data"][0]["embedding"]

In [21]:
# load all movie summary data into memory
plot_summaries = defaultdict(list)
for plot_summary_path in glob.glob('data/movies/*/plot_summaries/*.txt'):

    movie_id = plot_summary_path.split('/')[2]
    with open(plot_summary_path, 'r') as fp:
        plot_summaries[movie_id].append(fp.read())

In [22]:
flat_summaries = list()
for movie, summaries in plot_summaries.items():
    for summary in summaries:
        flat_summaries.append(summary)

In [23]:
# figure out how many tokens this is
total_tokens = 0
for summary in flat_summaries:
    total_tokens += num_tokens_from_string(summary, "cl100k_base")
# $0.0004 / 1K tokens
0.0004 * (total_tokens / 1000)

1.603248

In [24]:
# we can do 250k tokens per minute or 3k requests per minute
def rate_limit(tokens_processed: int, n_requests: int, next_input_token_count = int, token_limit: int = 250_000, request_limit: int = 3_000):
    return tokens_processed + next_input_token_count > token_limit or n_requests >= request_limit

def get_mins_elapsed(start_time):
    return int((time.time() - start_time) / 60)

In [25]:
# Load your API key from an environment variable or secret management service
with open('/Users/christopherolley/open-api-key.txt', 'r') as fp:
    openai.api_key = fp.read()

In [26]:
# let's process some embeddings
count = 0
start_time = time.time()
tokens_processed, n_requests, last_mins_elapsed = 0, 0, 0
total_tokens_processed, total_requests = 0, 0
token_limit = 250_000
request_limit = 3_000
movie_paths = glob.glob('data/movies/*/')
for movie_num, movie_path in enumerate(movie_paths):
    movie_id = movie_path.split('/')[2]
   # create folder for movie embeddings if necessary
    if not os.path.exists(f'data/embeddings_v1/{movie_id}'):
        os.makedirs(f'data/embeddings_v1/{movie_id}')
    for i, summary_path in enumerate(glob.glob(f'data/movies/{movie_id}/plot_summaries/*.txt')):
        mins_elapsed = get_mins_elapsed(start_time)
        print(f'Processing {movie_id} ({movie_num} / {len(movie_paths)}), Summary {i} - mins elapsed: {mins_elapsed}, n_requests: {n_requests} / {request_limit}, tokens_processed: {tokens_processed} / {token_limit}')
        processing_time_start = time.time()
        
        # check if this embedding has been processed
        if os.path.exists(f'data/embeddings_v1/{movie_id}/{i}.txt'):
            continue
        
        # get summary + number of tokens to process
        with open(summary_path, 'r') as fp:
            summary = fp.read()
        n_tokens = num_tokens_from_string(summary, "cl100k_base")
        
        # check if we need to wait until the end of the minute
        while rate_limit(tokens_processed, n_requests, n_tokens):
            print("Hit rate limit at, taking a break")
            time.sleep(1) # take a time out while at rate limit
            mins_elapsed = get_mins_elapsed(start_time)
            if mins_elapsed > last_mins_elapsed:
                tokens_processed, n_requests = 0, 0
        
        # we are good to go
        embedding = get_embedding(summary)
        with open(f'data/embeddings_v1/{movie_id}/{i}.txt', 'w') as fp:
            print(f'Writing data/embeddings_v1/{movie_id}/{i}.txt')
            fp.write(','.join([str(val) for val in embedding]))
        
        tokens_processed += n_tokens
        n_requests += 1
        total_tokens_processed += n_tokens
        total_requests += 1
        if mins_elapsed > last_mins_elapsed:
            tokens_processed, n_requests = 0, 0
        last_mins_elapsed = mins_elapsed
        print(f"Processing took: {time.time() - processing_time_start:.3f}s")
#         time.sleep(1) # take a time out between requests
print(f"Finished processing in {(time.time() - start_time) / 60:.3f} mins, processed {total_tokens_processed} tokens in {total_requests} requests.")

Processing tt1119646_the_hangover (0 / 11073), Summary 0 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt1119646_the_hangover (0 / 11073), Summary 1 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt1119646_the_hangover (0 / 11073), Summary 2 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt1119646_the_hangover (0 / 11073), Summary 3 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt1119646_the_hangover (0 / 11073), Summary 4 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt0349710_ladder_49 (1 / 11073), Summary 0 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt0349710_ladder_49 (1 / 11073), Summary 1 - mins elapsed: 0, n_requests: 0 / 3000, tokens_processed: 0 / 250000
Processing tt0026685_mark_of_the_vampire (2 / 11073), Summary 0 - mins elapsed: 0, n_requests: 0 / 3000, tokens_proce

Writing data/embeddings_v1/tt5253282_the_bachelors/0.txt
Processing took: 0.489s
Processing tt5253282_the_bachelors (18 / 11073), Summary 1 - mins elapsed: 0, n_requests: 22 / 3000, tokens_processed: 1919 / 250000
Writing data/embeddings_v1/tt5253282_the_bachelors/1.txt
Processing took: 0.424s
Processing tt0086250_scarface (19 / 11073), Summary 0 - mins elapsed: 0, n_requests: 23 / 3000, tokens_processed: 2051 / 250000
Processing tt0086250_scarface (19 / 11073), Summary 1 - mins elapsed: 0, n_requests: 23 / 3000, tokens_processed: 2051 / 250000
Processing tt0086250_scarface (19 / 11073), Summary 2 - mins elapsed: 0, n_requests: 23 / 3000, tokens_processed: 2051 / 250000
Processing tt0086250_scarface (19 / 11073), Summary 3 - mins elapsed: 0, n_requests: 23 / 3000, tokens_processed: 2051 / 250000
Processing tt0086250_scarface (19 / 11073), Summary 4 - mins elapsed: 0, n_requests: 23 / 3000, tokens_processed: 2051 / 250000
Processing tt0074860_marathon_man (20 / 11073), Summary 0 - mins 

Writing data/embeddings_v1/tt1726252_the_dark_side_of_the_moon/1.txt
Processing took: 0.527s
Processing tt4501244_why_him? (34 / 11073), Summary 0 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt4501244_why_him? (34 / 11073), Summary 1 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt4501244_why_him? (34 / 11073), Summary 2 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt4501244_why_him? (34 / 11073), Summary 3 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt0079522_manhattan (35 / 11073), Summary 0 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt0079522_manhattan (35 / 11073), Summary 1 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processing tt0079522_manhattan (35 / 11073), Summary 2 - mins elapsed: 0, n_requests: 37 / 3000, tokens_processed: 3968 / 250000
Processi

Writing data/embeddings_v1/tt0039220_brighton_rock/1.txt
Processing took: 0.104s
Processing tt2334649_fruitvale_station (50 / 11073), Summary 0 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt2334649_fruitvale_station (50 / 11073), Summary 1 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt2334649_fruitvale_station (50 / 11073), Summary 2 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt2334649_fruitvale_station (50 / 11073), Summary 3 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt0352248_cinderella_man (51 / 11073), Summary 0 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt0352248_cinderella_man (51 / 11073), Summary 1 - mins elapsed: 0, n_requests: 58 / 3000, tokens_processed: 5890 / 250000
Processing tt0352248_cinderella_man (51 / 11073), Summary 2 - mins elapsed: 0, n_requests: 58 / 3000, t

Writing data/embeddings_v1/tt0071155_the_apprenticeship_of_duddy_kravitz/1.txt
Processing took: 0.100s
Processing tt0071155_the_apprenticeship_of_duddy_kravitz (67 / 11073), Summary 2 - mins elapsed: 0, n_requests: 69 / 3000, tokens_processed: 6873 / 250000
Writing data/embeddings_v1/tt0071155_the_apprenticeship_of_duddy_kravitz/2.txt
Processing took: 0.158s
Processing tt0078326_straight_time (68 / 11073), Summary 0 - mins elapsed: 0, n_requests: 70 / 3000, tokens_processed: 6958 / 250000
Writing data/embeddings_v1/tt0078326_straight_time/0.txt
Processing took: 0.102s
Processing tt0078326_straight_time (68 / 11073), Summary 1 - mins elapsed: 0, n_requests: 71 / 3000, tokens_processed: 7103 / 250000
Writing data/embeddings_v1/tt0078326_straight_time/1.txt
Processing took: 0.495s
Processing tt0078326_straight_time (68 / 11073), Summary 2 - mins elapsed: 0, n_requests: 72 / 3000, tokens_processed: 7132 / 250000
Writing data/embeddings_v1/tt0078326_straight_time/2.txt
Processing took: 0.10

...

Writing data/embeddings_v1/tt0065963_the_landlord/1.txt
Processing took: 0.515s
Processing tt0065963_the_landlord (11006 / 11073), Summary 2 - mins elapsed: 75, n_requests: 3 / 3000, tokens_processed: 496 / 250000
Writing data/embeddings_v1/tt0065963_the_landlord/2.txt
Processing took: 0.364s
Processing tt4844148_mia_and_the_white_lion (11007 / 11073), Summary 0 - mins elapsed: 75, n_requests: 4 / 3000, tokens_processed: 689 / 250000
Writing data/embeddings_v1/tt4844148_mia_and_the_white_lion/0.txt
Processing took: 0.100s
Processing tt4844148_mia_and_the_white_lion (11007 / 11073), Summary 1 - mins elapsed: 75, n_requests: 5 / 3000, tokens_processed: 814 / 250000
Writing data/embeddings_v1/tt4844148_mia_and_the_white_lion/1.txt
Processing took: 0.936s
Processing tt4844148_mia_and_the_white_lion (11007 / 11073), Summary 2 - mins elapsed: 75, n_requests: 6 / 3000, tokens_processed: 941 / 250000
Writing data/embeddings_v1/tt4844148_mia_and_the_white_lion/2.txt
Processing took: 0.146s
Proc

Writing data/embeddings_v1/tt1656192_special_forces/2.txt
Processing took: 0.251s
Processing tt0111797_eat_drink_man_woman (11022 / 11073), Summary 0 - mins elapsed: 75, n_requests: 20 / 3000, tokens_processed: 2450 / 250000
Writing data/embeddings_v1/tt0111797_eat_drink_man_woman/0.txt
Processing took: 0.195s
Processing tt0111797_eat_drink_man_woman (11022 / 11073), Summary 1 - mins elapsed: 75, n_requests: 21 / 3000, tokens_processed: 2532 / 250000
Writing data/embeddings_v1/tt0111797_eat_drink_man_woman/1.txt
Processing took: 0.737s
Processing tt0111797_eat_drink_man_woman (11022 / 11073), Summary 2 - mins elapsed: 75, n_requests: 22 / 3000, tokens_processed: 2563 / 250000
Writing data/embeddings_v1/tt0111797_eat_drink_man_woman/2.txt
Processing took: 0.653s
Processing tt2345737_the_rover (11023 / 11073), Summary 0 - mins elapsed: 75, n_requests: 23 / 3000, tokens_processed: 2672 / 250000
Processing tt2345737_the_rover (11023 / 11073), Summary 1 - mins elapsed: 75, n_requests: 23 / 

Writing data/embeddings_v1/tt0093940_september/1.txt
Processing took: 0.999s
Processing tt0093940_september (11037 / 11073), Summary 2 - mins elapsed: 75, n_requests: 37 / 3000, tokens_processed: 4625 / 250000
Writing data/embeddings_v1/tt0093940_september/2.txt
Processing took: 0.474s
Processing tt0093940_september (11037 / 11073), Summary 3 - mins elapsed: 75, n_requests: 38 / 3000, tokens_processed: 4660 / 250000
Writing data/embeddings_v1/tt0093940_september/3.txt
Processing took: 0.166s
Processing tt0810784_bright_star (11038 / 11073), Summary 0 - mins elapsed: 75, n_requests: 39 / 3000, tokens_processed: 4707 / 250000
Processing tt0810784_bright_star (11038 / 11073), Summary 1 - mins elapsed: 75, n_requests: 39 / 3000, tokens_processed: 4707 / 250000
Processing tt0810784_bright_star (11038 / 11073), Summary 2 - mins elapsed: 75, n_requests: 39 / 3000, tokens_processed: 4707 / 250000
Processing tt0074258_burnt_offerings (11039 / 11073), Summary 0 - mins elapsed: 75, n_requests: 39

Writing data/embeddings_v1/tt0061369_asterix_the_gaul/1.txt
Processing took: 0.375s
Processing tt0061578_the_dirty_dozen (11052 / 11073), Summary 0 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt0061578_the_dirty_dozen (11052 / 11073), Summary 1 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt0061578_the_dirty_dozen (11052 / 11073), Summary 2 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt0061578_the_dirty_dozen (11052 / 11073), Summary 3 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt0061578_the_dirty_dozen (11052 / 11073), Summary 4 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt1515091_sherlock_holmes:_a_game_of_shadows (11053 / 11073), Summary 0 - mins elapsed: 75, n_requests: 62 / 3000, tokens_processed: 7205 / 250000
Processing tt1515091_sherlock_holmes:_a_game_of_shadows (11053 

Writing data/embeddings_v1/tt0032637_the_invisible_woman/0.txt
Processing took: 0.958s
Processing tt0032637_the_invisible_woman (11065 / 11073), Summary 1 - mins elapsed: 75, n_requests: 80 / 3000, tokens_processed: 9313 / 250000
Writing data/embeddings_v1/tt0032637_the_invisible_woman/1.txt
Processing took: 0.177s
Processing tt0032637_the_invisible_woman (11065 / 11073), Summary 2 - mins elapsed: 75, n_requests: 81 / 3000, tokens_processed: 9332 / 250000
Writing data/embeddings_v1/tt0032637_the_invisible_woman/2.txt
Processing took: 0.334s
Processing tt2908446_the_divergent_series:_insurgent (11066 / 11073), Summary 0 - mins elapsed: 75, n_requests: 82 / 3000, tokens_processed: 9426 / 250000
Processing tt2908446_the_divergent_series:_insurgent (11066 / 11073), Summary 1 - mins elapsed: 75, n_requests: 82 / 3000, tokens_processed: 9426 / 250000
Processing tt2908446_the_divergent_series:_insurgent (11066 / 11073), Summary 2 - mins elapsed: 75, n_requests: 82 / 3000, tokens_processed: 94